In [11]:
import mlflow
# Step 2: Set up the MLflow tracking server
mlflow.set_tracking_uri("http://ec2-18-141-141-49.ap-southeast-1.compute.amazonaws.com:5000")

In [12]:
mlflow.set_experiment("LightGBM HP Tuning")

<Experiment: artifact_location='s3://mlflow-bucket-vietnq/363964669577582014', creation_time=1754211015209, experiment_id='363964669577582014', last_update_time=1754211015209, lifecycle_stage='active', name='LightGBM HP Tuning', tags={}>

In [13]:
import pandas as pd

df = pd.read_csv('dataset.csv').dropna()
df.shape

(36662, 2)

In [14]:
import pandas as pd
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split, cross_val_score
from sklearn.metrics import accuracy_score, classification_report
from imblearn.over_sampling import SMOTE
import mlflow
import mlflow.sklearn
import optuna
from lightgbm import LGBMClassifier
import matplotlib.pyplot as plt

In [15]:
df['category'] = df['category'].map({-1:2, 0:0, 1:1})
df.dropna(subset=['category'])
df.shape

(36662, 2)

In [16]:
ngram_range = (1,3)
max_features = 1000
vectorizer = TfidfVectorizer(ngram_range=ngram_range, max_features= max_features)
X_train, X_test, y_train, y_test = train_test_split(df['clean_comment'], df['category'], test_size=0.2, random_state=42, stratify=df['category'])
X_train_vec = vectorizer.fit_transform(X_train)
X_test_vec = vectorizer.transform(X_test)

oversampler=SMOTE(random_state=42)
X_resampled, y_resampled = oversampler.fit_resample(X_train_vec, y_train)

In [17]:
# Function to log results in MLflow
def log_mlflow(model_name, model, X_train, X_test, y_train, y_test, params, trial_number):
    with mlflow.start_run():
        # Log model type and trial number
        mlflow.set_tag("mlflow.runName", f"Trial_{trial_number}_{model_name}_SMOTE_TFIDF_Trigrams")
        mlflow.set_tag("experiment_type", "algorithm_comparison")

        # Log algorithm name as a parameter
        mlflow.log_param("algo_name", model_name)

        # Log hyperparameters
        for key, value in params.items():
            mlflow.log_param(key, value)

        # Train model
        model.fit(X_train, y_train)
        y_pred = model.predict(X_test)

        # Log accuracy
        accuracy = accuracy_score(y_test, y_pred)
        mlflow.log_metric("accuracy", accuracy)

        # Log classification report
        classification_rep = classification_report(y_test, y_pred, output_dict=True)
        for label, metrics in classification_rep.items():
            if isinstance(metrics, dict):
                for metric, value in metrics.items():
                    mlflow.log_metric(f"{label}_{metric}", value)

        # Log the model
        mlflow.sklearn.log_model(model, f"{model_name}_model")

        return accuracy

In [18]:
def objective_lightgbm(trial):
    n_estimators = trial.suggest_int('n_estimators', 100, 1000)
    learning_rate = trial.suggest_float('learning_rate', 1e-4, 1e-1, log=True)
    max_depth = trial.suggest_int('max_depth', 3, 15)
    num_leaves = trial.suggest_int('num_leaves', 20, 150)
    min_child_samples = trial.suggest_int('min_child_samples', 10, 100)
    colsample_bytree = trial.suggest_float('colsample_bytree', 0.5, 1.0)
    subsample = trial.suggest_float('subsample', 0.5, 1.0)
    reg_alpha = trial.suggest_float('reg_alpha', 1e-4, 10.0, log=True)
    reg_lambda = trial.suggest_float('reg_lambda', 1e-4, 10.0, log=True)

    params = {
        'n_estimators': n_estimators,
        'learning_rate': learning_rate,
        'max_depth': max_depth,
        'num_leaves': num_leaves,
        'min_child_samples': min_child_samples,
        'colsample_bytree': colsample_bytree,
        'subsample': subsample,
        'reg_alpha': reg_alpha,
        'reg_lambda': reg_lambda
    }
    model = LGBMClassifier(**params, random_state=42, n_jobs=-1)
    accuracy = log_mlflow("LightGBM", model, X_resampled, X_test_vec, y_resampled, y_test, params, trial.number)

    return accuracy

In [19]:
def run_optuna_experiment():
    study = optuna.create_study(direction='maximize')
    study.optimize(objective_lightgbm, n_trials=100)

    best_params = study.best_params
    best_model = LGBMClassifier(**best_params, random_state=42)
    log_mlflow('LightGBM', best_model, X_resampled, X_test_vec, y_resampled, y_test, best_params, "Best")
    
    optuna.visualization.plot_param_importances(study).show()
    optuna.visualization.plot_optimization_history(study).show()


In [20]:
run_optuna_experiment()

[I 2025-08-03 16:25:40,829] A new study created in memory with name: no-name-e6f90f28-be8d-45d5-ae7b-0734a93c5e90


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.042687 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 99478
[LightGBM] [Info] Number of data points in the train set: 37848, number of used features: 969
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] N

/home/viet2005/workspace/self_project/youtube_comments_sentiment_analysis/venv/lib/python3.12/site-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(
2025/08/03 16:26:50 WARNING mlflow.models.model: `artifact_path` is deprecated. Please use `name` instead.
2025/08/03 16:26:56 WARNING mlflow.models.model: Model logged without a signature and input example. Please set `input_example` parameter when logging the model to auto infer the model signature.
[I 2025-08-03 16:27:02,000] Trial 0 finished with value: 0.6743488340379108 and parameters: {'n_estimators': 815, 'learning_rate': 0.0006555728860679289, 'max_depth': 9, 'num_leaves': 94, 'min_child_samples': 51, 'colsample_bytree': 0.500241969159719, 'subsample': 0.9722833603716574, 'reg_alpha': 0.00010267117054912717, 'reg_lambda': 1.7964416357903454}. Best is trial 0 with value: 0.6743488340379108.


🏃 View run Trial_0_LightGBM_SMOTE_TFIDF_Trigrams at: http://ec2-18-141-141-49.ap-southeast-1.compute.amazonaws.com:5000/#/experiments/363964669577582014/runs/062d170201c24ab38b35c62113219ad6
🧪 View experiment at: http://ec2-18-141-141-49.ap-southeast-1.compute.amazonaws.com:5000/#/experiments/363964669577582014
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.050063 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 99539
[LightGBM] [Info] Number of data points in the train set: 37848, number of used features: 975
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM

/home/viet2005/workspace/self_project/youtube_comments_sentiment_analysis/venv/lib/python3.12/site-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(
2025/08/03 16:28:11 WARNING mlflow.models.model: `artifact_path` is deprecated. Please use `name` instead.
2025/08/03 16:28:22 WARNING mlflow.models.model: Model logged without a signature and input example. Please set `input_example` parameter when logging the model to auto infer the model signature.
[I 2025-08-03 16:28:30,468] Trial 1 finished with value: 0.6453020591845083 and parameters: {'n_estimators': 953, 'learning_rate': 0.0010515297458615833, 'max_depth': 7, 'num_leaves': 60, 'min_child_samples': 21, 'colsample_bytree': 0.8037105554933042, 'subsample': 0.5988818900419992, 'reg_alpha': 0.0021783808265982327, 'reg_lambda': 0.030286887468811863}. Best is trial 0 with value: 0.6743488340379108.


...

/home/viet2005/workspace/self_project/youtube_comments_sentiment_analysis/venv/lib/python3.12/site-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(
2025/08/03 17:45:33 WARNING mlflow.models.model: `artifact_path` is deprecated. Please use `name` instead.
2025/08/03 17:45:38 WARNING mlflow.models.model: Model logged without a signature and input example. Please set `input_example` parameter when logging the model to auto infer the model signature.
[I 2025-08-03 17:45:42,721] Trial 99 finished with value: 0.7794899768171281 and parameters: {'n_estimators': 239, 'learning_rate': 0.07405004534925873, 'max_depth': 14, 'num_leaves': 23, 'min_child_samples': 94, 'colsample_bytree': 0.6075398642855065, 'subsample': 0.6741930796351516, 'reg_alpha': 0.00982568738343033, 'reg_lambda': 3.7901726264112363}. Best is trial 76 with value: 0.7946270285012955.


🏃 View run Trial_99_LightGBM_SMOTE_TFIDF_Trigrams at: http://ec2-18-141-141-49.ap-southeast-1.compute.amazonaws.com:5000/#/experiments/363964669577582014/runs/1cc836eee8bd4636861006b9de3f218a
🧪 View experiment at: http://ec2-18-141-141-49.ap-southeast-1.compute.amazonaws.com:5000/#/experiments/363964669577582014
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.051331 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 99580
[LightGBM] [Info] Number of data points in the train set: 37848, number of used features: 981
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Info] Start training from score -1.098612
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGB

/home/viet2005/workspace/self_project/youtube_comments_sentiment_analysis/venv/lib/python3.12/site-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMClassifier was fitted with feature names
  warnings.warn(
2025/08/03 17:46:05 WARNING mlflow.models.model: `artifact_path` is deprecated. Please use `name` instead.
2025/08/03 17:46:10 WARNING mlflow.models.model: Model logged without a signature and input example. Please set `input_example` parameter when logging the model to auto infer the model signature.


🏃 View run Trial_Best_LightGBM_SMOTE_TFIDF_Trigrams at: http://ec2-18-141-141-49.ap-southeast-1.compute.amazonaws.com:5000/#/experiments/363964669577582014/runs/5df9aa4b77b240afbbd295a049f70ead
🧪 View experiment at: http://ec2-18-141-141-49.ap-southeast-1.compute.amazonaws.com:5000/#/experiments/363964669577582014


ImportError: Tried to import 'plotly' but failed. Please make sure that the package is installed correctly to use this feature. Actual error: No module named 'plotly'.